[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/drive/1DlFxQdcPIpDPCrfE_4K9K3fRu67ALghq?usp=sharing)
# How to Get Furnished Finder Listings for Medium Term Rentals

## Overview
| Detail Tag            | Information                                                                                        |
|-----------------------|----------------------------------------------------------------------------------------------------|
| Originally Created By | Ariel Herrera arielherrera@analyticsariel.com |
| External References   | API |
| Input Datasets        | Source name |
| Output Datasets       | Source name |
| Input Data Source     | Pandas DataFrame |
| Output Data Source    | Pandas DataFrame |

## History
| Date         | Developed By  | Reason                                                |
|--------------|---------------|-------------------------------------------------------|
| 12th Sep 2024 | Ariel Herrera | Create notebook. |

## Getting Started
1. Copy this notebook -> File -> Save a Copy in Drive
2. Directions

## Useful Resources
- [Google Colab Cheat Sheet](https://towardsdatascience.com/cheat-sheet-for-google-colab-63853778c093)

## <font color="blue">Install Packages</font>

In [1]:
!pip install geopy -q

## <font color="blue">Imports</font>

In [2]:
import requests
import pandas as pd
import json
from datetime import datetime
from getpass import getpass
from google.colab import files
import plotly.express as px
from bs4 import BeautifulSoup
from geopy.geocoders import Nominatim
import random
from geopy.distance import geodesic

pd.set_option('display.max_columns', None)

## <font color="blue">Functions</font>

In [3]:
# Function to get latitude and longitude of address
def get_prop_address_lat_long(address):
    # Generate a random number between 1 and 10
    random_number = random.randint(1, 10)

    # Format the number with a leading zero if it's a single digit
    formatted_number = f"{random_number:02d}"

    # Initialize Nominatim API
    geolocator = Nominatim(user_agent=f"furnished_finder_{formatted_number}")

    # Get location of an address
    location = geolocator.geocode(address)

    if location:
        return location.latitude, location.longitude
    else:
        return None, None


# Function to calculate distance between two lat/lon points
def haversine_distance(lat1, lon1, lat2, lon2):
    return geodesic((lat1, lon1), (lat2, lon2)).miles


# Function to find the 10 nearest properties
def find_nearest_properties(df, latitude, longitude, n=10):
    # Calculate the distance from the input location to each property
    df['distance'] = df.apply(lambda row: haversine_distance(latitude, longitude, row['lat'], row['long']), axis=1)

    # Sort by distance and get the top n nearest properties
    df_nearest_props = df.sort_values(by='distance').head(n).reset_index(drop=True)
    df_nearest_props = df_nearest_props[[
        'unique_id', 'title', 'description', 'rental_price', 'distance',
        'PType', 'City', 'State', 'lat', 'long',
        'AvailDate', 'BedRoomCount', 'Furnished', 'Utilities', 'FreeParking', 'HouseKeeping', 'Wifi', 'Submitted_by', 'PILink']]

    return df_nearest_props

## <font color="blue">Locals & Constants</font>

In [4]:
api_key = getpass('Enter the scrapeak api key: ')

Enter the scrapeak api key: ··········


## <font color="blue">Data</font>

In [5]:
search_query = "Tampa, FL"
move_dt_default = datetime.today().strftime('%Y-%m-%d') # today's date

### <font color="green">1. Location Search</font>

Request data from API

In [6]:
# api endpoint and default headers
api_url = "https://app.scrapeak.com/v1/scrapers/furnished_finder/listing"

parameters = {
    "api_key":api_key,
    "searchType":"basic",
    "q":search_query,
    "moveInDate":move_dt_default,
    "monthlyBudgetMin":0,
    "monthlyBudgetMax":5000
}

# make the API request
response = requests.get(api_url, params=parameters)
response_content = response.text

print(response_content)

{"is_success":true,"data":[{"id":"575492_1","IsMultipleUnit":"False","name":"<div class='title' title='immaculate 1Br 1Bt close to Morton Plant...'>immaculate 1Br 1Bt close to Morton Plant...</div><div class='title_img'> <img src='https://www.furnishedfinder.com/images/verified.png' alt='Verified' title='Verified Property' ></div>","lat":27.9637922,"long":-82.7795766,"MDesc":"<ul><li>Fully Furnished</li><li>Utilities Included</li><li>1 bedroom</li></ul>","MDesc2":"$1,500/month","PType":"Apartment","PF":"False","image":"https://static.furnishedfinder.com/575492/1/575492_1_51009745-300-300.jpeg","PILink":"https://www.furnishedfinder.com/property/575492_1","Icon":"","Price":"$1,500","Avail":"Contact for Availability","AvailDate":"8/27/2023","City":"Clearwater","State":"Florida","Preferred":"True","Verified":"True","BathType":"Private Bath","LNRLink":"","camount":"0","BedRoomCount":"1","ExternalCode":"","Furnished":"True","Utilities":"True","HotTub":"False","FreeParking":"True","HouseKeepi

View API response

In [7]:
# view data keys
response.json().keys()

dict_keys(['is_success', 'data', 'message', 'info'])

In [8]:
# view number of credits used
response.json()['info']

{'used_credits': 20, 'remaining_credits': 49940}

In [9]:
len(response.json()['data'])

2360

Transform response into a dataframe (rows and columns)

In [10]:
df_listings = pd.DataFrame(response.json()['data'])
df_listings['unique_id'] = df_listings.apply(lambda x: x['id'].split('_')[0], axis=1)
df_listings['title'] = df_listings.apply(lambda x: x['name'].split("title='")[1].split("'>")[0], axis=1)
df_listings['description'] = df_listings.apply(lambda x: BeautifulSoup(x['MDesc'], "html.parser").get_text(separator=". "), axis=1)
df_listings['rental_price'] = df_listings.apply(lambda x: int(x['Price'].replace("$", "").replace(",", "")), axis=1)
print('Number of columns:', len(df_listings.columns))
print('Number of rows:', len(df_listings))
df_listings.head()

Number of columns: 51
Number of rows: 2360


id IsMultipleUnit                                               name  \
0  575492_1          False  <div class='title' title='immaculate 1Br 1Bt c...   
1  705149_4          False  <div class='title' title='Unit 1'>Unit 1</div>...   
2  705149_5          False  <div class='title' title='Unit 7'>Unit 7</div>...   
3  742962_1          False  <div class='title' title='One bedroom waterfro...   
4  694486_1          False  <div class='title' title='Island Estates Clear...   

         lat       long                                              MDesc  \
0  27.963792 -82.779577  <ul><li>Fully Furnished</li><li>Utilities Incl...   
1  27.834247 -82.833763  <ul><li>Fully Furnished</li><li>Utilities Incl...   
2  27.834247 -82.833763  <ul><li>Fully Furnished</li><li>Utilities Incl...   
3  27.812966 -82.794443  <ul><li>Fully Furnished</li><li>Utilities Incl...   
4  27.980312 -82.819828  <ul><li>Fully Furnished</li><li>1 bedroom</li>...   

         MDesc2      PType     PF  \
0  $1,500/month  Apartment  False   
1  $2,700/month  Apartment   True   
2  $2,000/month  Apartment   True   
3  $1,600/month  Apartment  False   
4  $2,500/month  Apartment  False   

                                               image  \
0  https://static.furnishedfinder.com/575492/1/57...   
1  https://static.furnishedfinder.com/705149/4/70...   
2  https://static.furnishedfinder.com/705149/5/70...   
3  https://static.furnishedfinder.com/742962/1/74...   
4  https://static.furnishedfinder.com/694486/1/69...   

                                              PILink Icon   Price  \
0  https://www.furnishedfinder.com/property/575492_1       $1,500   
1  https://www.furnishedfinder.com/property/705149_4       $2,700   
2  https://www.furnishedfinder.com/property/705149_5       $2,000   
3  https://www.furnishedfinder.com/property/742962_1       $1,600   
4  https://www.furnishedfinder.com/property/694486_1       $2,500   

                            Avail  AvailDate              City    State  \
0        Contact for Availability  8/27/2023        Clearwater  Florida   
1        Contact for Availability   9/1/2024  Redington Shores  Florida   
2        Contact for Availability   9/1/2024  Redington Shores  Florida   
3  Available On<br />September 15  9/15/2024     Madeira Beach  Florida   
4                       Available  9/10/2024  Clearwater Beach  Florida   

  Preferred Verified      BathType LNRLink camount BedRoomCount ExternalCode  \
0      True     True  Private Bath               0            1                
1      True     True  Private Bath               0            2                
2      True     True  Private Bath               0            1                
3      True     True  Private Bath               0            1                
4      True     True  Private Bath               0            1                

  Furnished Utilities HotTub FreeParking HouseKeeping  Wifi   Pool SmartTV  \
0      True      True  False        True        False  True  False   False   
1      True      True  False        True        False  True  False    True   
2      True      True  False        True        False  True  False    True   
3      True      True  False        True        False  True   True    True   
4      True     False  False        True        False  True   True    True   

  Laundry KingSizeBed     EV Kitchen WheelChair    Gym Score PMScore  \
0    True       False  False    True      False  False  1000       0   
1    True       False  False    True      False  False  1000       0   
2    True       False  False    True      False  False  1000       0   
3    True       False  False    True      False   True  1000       0   
4    True       False  False    True      False  False  1000       0   

  QualityScore brand Subbrand ComplexPartner     Submitted_by  \
0            0             ,           False     Paul.Charles   
1            0             ,           False   emily.joseph37   
2            0             ,           False   em

View characteristics of the data

In [11]:
# prompt: create me a bar graph from df_listings in plotly to get number of total listings per city
df_listings_by_city = df_listings.groupby(['City'])['unique_id'].count().reset_index().sort_values(by='unique_id', ascending=False)
fig = px.histogram(df_listings_by_city, x="City", y='unique_id', title="Total Listings per City")
fig.show()

Group data by property type and beds

In [12]:
# group data to segment information by location and property attributes
df_listings_grp = df_listings.groupby(['State', 'City', 'PType', 'BedRoomCount']).agg(
    count=('unique_id', 'count'),
    median_rental_price=('rental_price', 'median'),
    max_rental_price=('rental_price', 'max'),
    min_rental_price=('rental_price', 'min')
).reset_index().sort_values(by=['State', 'City', 'PType', 'BedRoomCount']).reset_index(drop=True)
df_listings_grp

State           City      PType BedRoomCount  count  \
0    Florida   Apollo Beach  Apartment            1      1   
1    Florida   Apollo Beach      Condo            2      3   
2    Florida   Apollo Beach      House            2      2   
3    Florida   Apollo Beach      House            3      4   
4    Florida   Apollo Beach      House            4      3   
..       ...            ...        ...          ...    ...   
352  Florida  Wesley Chapel      House            4      3   
353  Florida  Wesley Chapel      House            5      1   
354  Florida  Wesley Chapel       Room            1     29   
355  Florida        Wimauma       Room            1      5   
356  Florida    Zephyrhills      House            3      1   

     median_rental_price  max_rental_price  min_rental_price  
0                 2500.0              2500              2500  
1                 2500.0              3500              1700  
2                 2150.0              2300              2000  
3                 3850.0              4590              3000  
4                 4500.0              5000              2700  
..                   ...               ...               ...  
352               3950.0              4500              2800  
353               3950.0              3950              3950  
354               1200.0              1500               800  
355               1000.0              1800               800  
356               3495.0              3495              3495  

[357 rows x 8 columns]

View in-depth analysis

In [13]:
# 1. Select parameters
select_city = 'Tampa'
select_bedroom_count = '1'

# 2. Filter on city
df_listings_city = df_listings_grp.loc[
    (df_listings_grp['City'] == select_city) &
    (df_listings_grp['BedRoomCount'] == select_bedroom_count)].reset_index(drop=True)
print('Median rental price across property types: $', df_listings_city['median_rental_price'].median())
df_listings_city

Median rental price across property types: $ 1800.0


State   City      PType BedRoomCount  count  median_rental_price  \
0  Florida  Tampa  Apartment            1     69               1800.0   
1  Florida  Tampa      Condo            1     16               2550.0   
2  Florida  Tampa    Cottage            1     15               1750.0   
3  Florida  Tampa      House            1     30               1975.0   
4  Florida  Tampa       Room            1    166               1200.0   

   max_rental_price  min_rental_price  
0              4500              1000  
1              3500              1300  
2              2550              1200  
3              5000              1250  
4              5000               750

### <font color="green">2. Comparables Search</font>

Review listings near subject property

In [14]:
prop_address = "1912 E Emma St, Tampa, FL 33610" # enter in an address
prop_lat, prop_long = get_prop_address_lat_long(prop_address)
print(prop_lat, prop_long)

27.985920632653063 -82.43846624489795


Filter on listings for your comparables analysis

In [15]:
df_sub_listings = df_listings.loc[
    (df_listings['City'] == select_city) &
     (df_listings['BedRoomCount'] == select_bedroom_count) &
    (df_listings['PType'] == 'Room')].reset_index(drop=True)
df_sub_listings.head()

id IsMultipleUnit                                               name  \
0  698254_1          False  <div class='title' title='Quiet, Peaceful, Pro...   
1  668675_1          False  <div class='title' title='Central condo near T...   
2  678524_1          False  <div class='title' title='South Tampa room to ...   
3  526944_1          False  <div class='title' title='Private bedroom/bath...   
4  733581_1          False  <div class='title' title='3 bedroom condo priv...   

         lat       long                                              MDesc  \
0  27.982250 -82.569361  <ul><li>Fully Furnished</li><li>Utilities Incl...   
1  27.960293 -82.516144  <ul><li>Fully Furnished</li><li>Utilities Incl...   
2  27.885970 -82.520180  <ul><li>Fully Furnished</li><li>Utilities Incl...   
3  27.903989 -82.508055  <ul><li>Fully Furnished</li><li>Utilities Incl...   
4  27.982375 -82.559782  <ul><li>Fully Furnished</li><li>Utilities Incl...   

         MDesc2 PType     PF  \
0  $1,200/month  Room  False   
1  $1,300/month  Room   True   
2  $1,500/month  Room  False   
3  $1,200/month  Room  False   
4  $1,200/month  Room  False   

                                               image  \
0  https://static.furnishedfinder.com/698254/1/69...   
1  https://static.furnishedfinder.com/668675/1/66...   
2  https://static.furnishedfinder.com/678524/1/67...   
3  https://static.furnishedfinder.com/526944/1/52...   
4  https://static.furnishedfinder.com/733581/1/73...   

                                              PILink               Icon  \
0  https://www.furnishedfinder.com/property/698254_1  /images/roomH.png   
1  https://www.furnishedfinder.com/property/668675_1  /images/roomH.png   
2  https://www.furnishedfinder.com/property/678524_1  /images/roomH.png   
3  https://www.furnishedfinder.com/property/526944_1  /images/roomH.png   
4  https://www.furnishedfinder.com/property/733581_1  /images/roomH.png   

    Price                     Avail  AvailDate   City    State Preferred  \
0  $1,200                 Available   9/8/2024  Tampa  Florida      True   
1  $1,300  Contact for Availability  3/15/2024  Tampa  Florida      True   
2  $1,500  Contact for Availability   8/1/2024  Tampa  Florida      True   
3  $1,200  Contact for Availability  5/29/2023  Tampa  Florida      True   
4  $1,200  Contact for Availability   9/1/2024  Tampa  Florida      True   

  Verified      BathType LNRLink camount BedRoomCount ExternalCode Furnished  \
0     True  Private Bath               0            1                   True   
1     True  Private Bath               0            1                   True   
2     True  Private Bath               0            1                   True   
3     True  Private Bath               0            1                   True   
4     True  Private Bath               0            1                   True   

  Utilities HotTub FreeParking HouseKeeping  Wifi   Pool SmartTV Laundry  \
0      True   True        True        False  True   True   False    True   
1      True  False       False        False  True   True    True    True   
2      True   True        True         True  True   True    True    True   
3      True  False        True         True  True  False    True    True   
4      True  False        True        False  True   True    True    True   

  KingSizeBed     EV Kitchen WheelChair    Gym Score PMScore QualityScore  \
0       False  False    True      False   True  1000       0            0   
1       False  False    True       True   True  1000       0            0   
2       False  False   False      False  False  1000       0            0   
3       False  False    True      False   True     0       0            0   
4       False  False    True      False  False  1000       0            0   

  brand Subbrand ComplexPartner      Submitted_by  \
0             ,           False      jason.strong   
1             ,           False     Adriel.Flores   
2             ,           False     philip.morgan   
3 

Find nearest comparables

In [16]:
# find nearest listings based on distance to subject property
df_nearest_props = find_nearest_properties(df_sub_listings, prop_lat, prop_long, n=5)
df_nearest_props

unique_id                                              title  \
0    672288  Special room with private entrance and private...   
1    677817                                  Close to Hospital   
2    527529                           Beautiful home near ybor   
3    634490      One Bedroom with Private Bath in  a single...   
4    586404                                Beautiful Townhouse   

                                         description  rental_price  distance  \
0  Fully Furnished. Utilities Included. Room in a...          1200  0.293931   
1  Fully Furnished. Utilities Included. Room in a...          1200  0.560319   
2  Fully Furnished. Utilities Included. Room in a...           800  0.752811   
3  Fully Furnished. Utilities Included. Room in a...          1700  0.859588   
4  Fully Furnished. Utilities Included. Room in a...          1200  0.879939   

  PType   City    State        lat       long  AvailDate BedRoomCount  \
0  Room  Tampa  Florida  27.982150 -82.440720  3/16/2024            1   
1  Room  Tampa  Florida  27.983886 -82.429591  5/26/2024            1   
2  Room  Tampa  Florida  27.978305 -82.429630  7/18/2024            1   
3  Room  Tampa  Florida  27.976865 -82.448145  1/21/2024            1   
4  Room  Tampa  Florida  27.988963 -82.452448   1/1/2024            1   

  Furnished Utilities FreeParking HouseKeeping  Wifi        Submitted_by  \
0      True      True       False        False  True   lynette.grandison   
1      True      True        True        False  True        Brittcrowder   
2      True      True        True         True  True     Michael.Brown54   
3      True      True        True        False  True  jocelyn.moore_hill   
4      True      True        True        False  True          sarah.etti   

                                              PILink  
0  https://www.furnishedfinder.com/property/672288_1  
1  https://www.furnishedfinder.com/property/677817_1  
2  https://www.furnishedfinder.com/property/527529_1  
3  https://www.furnishedfinder.com/property/634490_1  
4  https://www.furnishedfinder.com/property/586404_1

### <font color="green">3. Visualize Comparables</font>

In [17]:
# View data
fig = px.scatter_mapbox(df_nearest_props,
                        lat="lat",
                        lon="long",
                        hover_name="title",
                        hover_data=["rental_price", "distance"],
                        color="rental_price",
                        size="rental_price",
                        zoom=14,
                        height=600,
                        size_max=20, # Adjust marker size
                        mapbox_style="carto-positron")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()


In [18]:
# calculate potential income
# note: this is a crude way of calculating income - ideally you'd want to factor expenses and vacancy rate
subj_property_bds = 4
est_rent_by_bd = 1200
print('Potential income: $', subj_property_bds * est_rent_by_bd)

Potential income: $ 4800


## <font color="blue">Output</font>

In [ ]:
# prompt: download df_listings to a csv file
df_listings.to_csv('listings.csv', index=False)
files.download('listings.csv')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
# [OPTIONAL] export into a csv file
file_name = 'output.csv'
df_listings.to_csv(file_name, index=False)
files.download(file_name)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# End Notebook